In [1]:
from lxml import etree
import requests
import pandas as pd

To get the MMS ID for a given barcode, get the metadata via `https://obv-at-oenb.alma.exlibrisgroup.com/view/sru/43ACC_ONB?version=1.2&query=alma.barcode=<barcode>startRecord=0&maximumRecords=1&operation=searchRetrieve&recordSchema=dc` and extract the MMS ID with `/srw:searchRetrieveResponse/srw:records/srw:record/srw:recordIdentifier/text()`.

Linked Data from ALMA (library management system) can be retrieved in 

* BIBFRAME via `https://open-na.hosted.exlibrisgroup.com/alma/<institution code>/bf/entity/instance/<mms id>`
* JSON-LD via `https://open-na.hosted.exlibrisgroup.com/alma/<institution code>/bibs/<mms_id>.jsonld`
* RDA/RDF via `https://open-na.hosted.exlibrisgroup.com/alma/<institution code>/rda/entity/manifestation/<mms id>.rdf`

For a Network Zone MMS ID the institution code is 43ACC_NETWORK and for the Institution MMS ID it is 43ACC_ONB.

The following xpath `/rdf:RDF/bf:Instance/bf:hasItem/bf:Item/bf:electronicLocator/rdfs:Resource/bflc:locator/@rdf:resource` selects URLs of the Viewer. We use the + sign (URL encoded %2B) to spilt the URL in order to extract the Barcode.

In [2]:
def getMMS_ID(barcode):
    cont=requests.get('https://obv-at-oenb.alma.exlibrisgroup.com/view/sru/43ACC_ONB?version=1.2&query=alma.barcode=%2BZ' + barcode + '&startRecord=0&maximumRecords=1&operation=searchRetrieve&recordSchema=dc').content
    e = etree.XML(cont)
    namespaces = {
        'srw': 'http://www.loc.gov/zing/srw/'
    }
    result = e.xpath('/srw:searchRetrieveResponse/srw:records/srw:record/srw:recordIdentifier/text()', namespaces=namespaces)
    return result[0]

def getLinksAndBarcodes(local_mms_id):
    cont=requests.get('https://open-na.hosted.exlibrisgroup.com/alma/43ACC_ONB/bf/entity/instance/' + local_mms_id).content
    e = etree.XML(cont)
    namespaces = {
        'rdf': 'http://www.w3.org/1999/02/22-rdf-syntax-ns#',
        'bf': 'http://id.loc.gov/ontologies/bibframe/',
        'rdfs': 'http://www.w3.org/2000/01/rdf-schema#',
        'bflc': 'http://id.loc.gov/ontologies/bflc/'
    }
    result = e.xpath('/rdf:RDF/bf:Instance/bf:hasItem/bf:Item/bf:electronicLocator/rdfs:Resource/bflc:locator/@rdf:resource', namespaces=namespaces)
    barcodes = []
    for link in result:
        splits = link.split('%2B')
        if len(splits) >= 2:
            barcodes.append('+' + link.split('%2B')[1])
    print(local_mms_id + ': ' + ", ".join(barcodes))
    linksJoined = ", ".join(result)
    barcodesJoined = ", ".join(barcodes)
    #returns a list with URLs and Barcodes
    return [linksJoined, barcodesJoined]

In [3]:
mms_id = getMMS_ID(str(255756803))
getLinksAndBarcodes(str(mms_id))

990035648370603338: +Z219890307, +Z255756803


['http://data.onb.ac.at/ABO/%2BZ219890307, http://data.onb.ac.at/ABO/%2BZ255756803',
 '+Z219890307, +Z255756803']